In [1]:
import h5py,glob,os
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
from pycbc.inference import io, models
from pycbc.workflow import WorkflowConfigParser
from pycbc import conversions, detector
import lal, lalsimulation as lalsim
# PLOTTING OPTIONS
fig_width_pt = 3*246.0  # Get this from LaTeX using \showthe\columnwidth
inches_per_pt = 1.0/72.27               # Convert pt to inch
golden_mean = (np.sqrt(5)-1.0)/2.0         # Aesthetic ratio
fig_width = fig_width_pt*inches_per_pt  # width in inches
fig_height = fig_width*golden_mean      # height in inches
fig_size =  [fig_width,fig_height]

params = { 'axes.labelsize': 24,
          'font.family': 'serif',
          'font.serif': 'Computer Modern Raman',
          'font.size': 24,
          'legend.fontsize': 20,
          'xtick.labelsize': 24,
          'ytick.labelsize': 24,
          'axes.grid' : True,
          'text.usetex': True,
          'savefig.dpi' : 100,
          'lines.markersize' : 14,
          'figure.figsize': fig_size}

mpl.rcParams.update(params)

In [2]:
lalparams = lal.CreateDict()
mode_array = [[2,2],[2,1],[3,3],[4,4]]
ModeArray = lalsim.SimInspiralCreateModeArray()
for mode in mode_array:
    print(mode)
    lalsim.SimInspiralModeArrayActivateMode(ModeArray, mode[0], mode[1])

[2, 2]
[2, 1]
[3, 3]
[4, 4]


In [5]:
ModeArray

<Swig Object of type 'tagLALValue *' at 0x7f44480b1340>

In [6]:
lalsim.SimInspiralWaveformParamsInsertModeArray(lalparams, ModeArray)

0

In [7]:
lalparams

<Swig Object of type 'tagLALDict *' at 0x7f44480b12d0>

In [8]:
common_pars=dict(
    m1=50*lal.MSUN_SI,
    m2=30*lal.MSUN_SI,
    S1x=0.5,
    S1y=0.,
    S1z=0.,
    S2x=0.,
    S2y=0.,
    S2z=0.,
    distance=1,
    inclination=np.pi/3.,
    phiRef=0.,
    longAscNodes=0.,
    eccentricity=0.,
    meanPerAno=0.,
    deltaF=1./4.,
    f_min=30.,
    f_max=512.,
    f_ref=30.,
    LALpars=lalparams,
    approximant=lalsim.IMRPhenomXPHM
    )

In [9]:
pars1=common_pars.copy()
pars2=common_pars.copy()
pars2.update({"m2":20.*lal.MSUN_SI})

In [11]:
hp1, hc1 = lalsim.SimInspiralChooseFDWaveform(**pars1)
hp2, hc2 = lalsim.SimInspiralChooseFDWaveform(**pars2)

In [12]:
def get_amp_phase(h):
    amp = np.abs(h)
    phase = np.unwrap(np.angle(h))
    return amp, phase

def sum_sqr_diff(x, y):
    return np.sqrt( np.sum( (x-y)**2 )  )

In [13]:
# compute amp and phase
hp1_amp, hp1_phase = get_amp_phase(hp1.data.data)
hc1_amp, hc1_phase = get_amp_phase(hc1.data.data)

hp2_amp, hp2_phase = get_amp_phase(hp2.data.data)
hc2_amp, hc2_phase = get_amp_phase(hc2.data.data)

hp_amp_diff = sum_sqr_diff(hp1_amp, hp2_amp)
hp_phase_diff = sum_sqr_diff(hp1_phase, hp2_phase)

hc_amp_diff = sum_sqr_diff(hc1_amp, hc2_amp)
hc_phase_diff = sum_sqr_diff(hc1_phase, hc2_phase)

In [14]:
print(hp_amp_diff,hp_phase_diff,hc_amp_diff,hc_phase_diff)

1166.011073432472 334.3756420016339 767.8213461946881 326.0800374360313


In [15]:
expected_result = np.array([1166.0110734324703, 334.37564200163365, 767.8213461946891, 326.0800374360311])

# PyCBC frequency domain waveform

In [17]:
#https://github.com/GeraintPratten/WaveformTutorialTest/blob/main/waveforms_tutorial.ipynb

In [19]:
from pycbc.waveform.generator import FDomainDetFrameGenerator
from pycbc import waveform

In [22]:
FDomainDetFrameGenerator?

In [23]:
generator = FDomainDetFrameGenerator(
    waveform.generator.FDomainCBCGenerator, 
    0., 
    variable_args=['mass1', 'mass2', 'spin1z', 'spin2z', 'tc', 'ra', 'dec', 'polarization'], 
    detectors=['H1', 'L1'], 
    delta_f=1./64, 
    f_lower=20., 
    approximant='SEOBNRv2_ROM_DoubleSpin')

In [24]:
generator.generate(mass1=38.6, mass2=29.3, spin1z=0.33, spin2z=-0.94, tc=2.43, ra=1.37, dec=-1.26, polarization=2.76)

{'H1': <pycbc.types.frequencyseries.FrequencySeries at 0x7f43bf283cc0>,
 'L1': <pycbc.types.frequencyseries.FrequencySeries at 0x7f43abf24550>}